In [20]:
import yt
from yt .mods import *
from yt import YTArray
import pandas as pd
import numpy as np
import ShapeTensor as st
import bisect
import time
import pickle
import matplotlib.pyplot as plt

In [21]:
from yt.units import kpc
from yt.units import Myr
from yt.units import Msun  

In [22]:
import os
import glob
import shutil
import os
from random import choice
from string import ascii_uppercase

In [23]:
#Disables annoying warnings when creating new columns in sgal_shape_df, expands visibility of dataframes
pd.options.mode.chained_assignment = None
pd.set_option('display.max_columns',500)
pd.set_option('display.max_rows',700)

In [24]:
path = r'/vol/sci/astro/bigdata/tussbaum/halofinder/catalog/'
sim_cat        = pd.read_pickle(path + 'sim_table.pkl')
sim_cat.set_index(['sid'], inplace=True)

In [66]:
path = r'/vol/sci/astro/bigdata/tussbaum/halofinder/catalog/'
cen_gal_cat    = pd.read_pickle(path + 'cen_gal_cat.pkl')
sim_cat        = pd.read_pickle(path + 'sim_table.pkl')
sim_cat.set_index(['sid'], inplace=True)
sgal_cat       = pd.read_pickle(path + 'sat_gal_table.pkl')
sgal_cat.set_index(['sgal_id'], inplace=True)
uniq_cat       = pd.read_pickle(path + 'tgal_tmp_thick_table.pkl')
sgal_attributes_cat = pd.read_pickle(path + 'gal_R_attribute_cat.pkl')
sgal_attributes_cat.set_index(['sgal_id'], inplace=True)
sgal_special_attribute_cat1 = pd.read_pickle(path + 'sgal_special_attribute_cat.profile_Rcoldgas.20180603.pkl')
sgal_special_attribute_cat2 = pd.read_pickle(path + 'sgal_special_attribute_cat.profiles.forces.pkl')
sgal_special_attribute_cat3 = pd.read_pickle(path + 'sgal_special_attribute_cat.profiles.pkl')

In [6]:
from multiprocessing import Pool, cpu_count, current_process



dest_path = ''
log_filename = dest_path + 'sgal_shape_df_tmp.log.log'
log_file = open(log_filename, 'w')

In [25]:
## Create a random path for the temporary folder in local hard disk /tmp/ folder. 
## In this example the name of the folder is a random string of 12 upper case letters.
_TMP_PATH_ = '/tmp/' + ''.join(choice(ascii_uppercase) for i in range(12))

path_1 = r'/vol/sci/astro/home/adambeilialpha/'

## Create temp folder on local disk if dosn't exist.
if not os.path.exists(_TMP_PATH_):
    os.makedirs(_TMP_PATH_)  
     
def copy_to_tmp(path,galaxynumber, index):
    for file in glob.glob(path+'VELA_v2/VELA_v2_'+galaxynumber+'*/*'+index[1:]+'*'):
        shutil.copy(file, _TMP_PATH_)  

                
def purge(pattern):
    for f in glob.glob(_TMP_PATH_ + "/*" + pattern + "*"):
        os.remove(f)       

In [33]:
#to delete the tmp folder
shutil.rmtree(_TMP_PATH_)

In [ ]:
### PAST HERE WILL BE CLEANED SOON, AS SOON AS I GET THIS TMP AND PURGE STUFF INSTALLED.

In [26]:
path_1 = r'/vol/sci/astro/home/adambeilialpha/'
sgal_shape_df = pd.read_pickle(path_1 + r'/sgal_temp_725_dm_all_3am_all.pkl')

In [9]:
sgal_shape_df[:150]

sim_id  \
VELA_v2.Thick.01.a0.190054357052_00002  VELA_v2.Thick.01.a0.190054357052   
VELA_v2.Thick.01.a0.200042665005_00002  VELA_v2.Thick.01.a0.200042665005   
VELA_v2.Thick.01.a0.21007348597_00005    VELA_v2.Thick.01.a0.21007348597   
VELA_v2.Thick.01.a0.220076084137_00001  VELA_v2.Thick.01.a0.220076084137   
VELA_v2.Thick.01.a0.230048596859_00003  VELA_v2.Thick.01.a0.230048596859   
VELA_v2.Thick.01.a0.240084543824_00004  VELA_v2.Thick.01.a0.240084543824   
VELA_v2.Thick.01.a0.250049263239_00005  VELA_v2.Thick.01.a0.250049263239   
VELA_v2.Thick.01.a0.250049263239_00008  VELA_v2.Thick.01.a0.250049263239   
VELA_v2.Thick.01.a0.26014688611_00001    VELA_v2.Thick.01.a0.26014688611   
VELA_v2.Thick.01.a0.26014688611_00003    VELA_v2.Thick.01.a0.26014688611   
VELA_v2.Thick.01.a0.26014688611_00004    VELA_v2.Thick.01.a0.26014688611   
VELA_v2.Thick.01.a0.26014688611_00007    VELA_v2.Thick.01.a0.26014688611   
VELA_v2.Thick.01.a0.270097225904_00005  VELA_v2.Thick.01.a0.270097225904   
VELA_v2.Thick.01.a0.270097225904_00006  VELA_v2.Thick.01.a0.270097225904   
VELA_v2.Thick.01.a0.270097225904_00007  VELA_v2.Thick.01.a0.270097225904   
VELA_v2.Thick.01.a0.280026525259_00005  VELA_v2.Thick.01.a0.280026525259   
VELA_v2.Thick.01.a0.280026525259_00006  VELA_v2.Thick.01.a0.280026525259   
VELA_v2.Thick.01.a0.280026525259_00007  VELA_v2.Thick.01.a0.280026525259   
VELA_v2.Thick.01.a0.290181875229_00004  VELA_v2.Thick.01.a0.290181875229   
VELA_v2.Thick.01.a0.290181875229_00005  VELA_v2.Thick.01.a0.290181875229   
VELA_v2.Thick.01.a0.290181875229_00006  VELA_v2.Thick.01.a0.290181875229   
VELA_v2.Thick.01.a0.300109177828_00002  VELA_v2.Thick.01.a0.300109177828   
VELA_v2.Thick.01.a0.300109177828_00004  VELA_v2.Thick.01.a0.300109177828   
VELA_v2.Thick.01.a0.300109177828_00007  VELA_v2.Thick.01.a0.300109177828   
VELA_v2.Thick.01.a0.300109177828_00009  VELA_v2.Thick.01.a0.300109177828   
VELA_v2.Thick.01.a0.310190021992_00002  VELA_v2.Thick.01.a0.310190021992   
VELA_v2.Thick.01.a0.310190021992_00006  VELA_v2.Thick.01.a0.310190021992   
VELA_v2.Thick.01.a0.310190021992_00007  VELA_v2.Thick.01.a0.310190021992   
VELA_v2.Thick.01.a0.310190021992_00011  VELA_v2.Thick.01.a0.310190021992   
VELA_v2.Thick.01.a0.320046544075_00003  VELA_v2.Thick.01.a0.320046544075   
VELA_v2.Thick.01.a0.320046544075_00008  VELA_v2.Thick.01.a0.320046544075   
VELA_v2.Thick.01.a0.320046544075_00009  VELA_v2.Thick.01.a0.320046544075   
VELA_v2.Thick.01.a0.320046544075_00011  VELA_v2.Thick.01.a0.320046544075   
VELA_v2.Thick.01.a0.330048590899_00005  VELA_v2.Thick.01.a0.330048590899   
VELA_v2.Thick.01.a0.330048590899_00006  VELA_v2.Thick.01.a0.330048590899   
VELA_v2.Thick.01.a0.330048590899_00007  VELA_v2.Thick.01.a0.330048590899   
VELA_v2.Thick.01.a0.330048590899_00009  VELA_v2.Thick.01.a0.330048590899   
VELA_v2.Thick.01.a0.340088844299_00004  VELA_v2.Thick.01.a0.340088844299   
VELA_v2.Thick.01.a0.340088844299_00006  VELA_v2.Thick.01.a0.340088844299   
VELA_v2.Thick.01.a0.340088844299_00007  VELA_v2.Thick.01.a0.340088844299   
VELA_v2.Thick.01.a0.340088844299_00008  VELA_v2.Thick.01.a0.340088844299   
VELA_v2.Thick.01.a0.350135147572_00002  VELA_v2.Thick.01.a0.350135147572   
VELA_v2.Thick.01.a0.350135147572_00008  VELA_v2.Thick.01.a0.350135147572   
VELA_v2.Thick.01.a0.350135147572_00010  VELA_v2.Thick.01.a0.350135147572   
VELA_v2.Thick.01.a0.350135147572_00011  VELA_v2.Thick.01.a0.350135147572   
VELA_v2.Thick.01.a0.360101670027_00002  VELA_v2.Thick.01.a0.360101670027   
VELA_v2.Thick.01.a0.360101670027_00003  VELA_v2.Thick.01.a0.360101670027   
VELA_v2.Thick.01.a0.360101670027_00007  VELA_v2.Thick.01.a0.360101670027   
VELA_v2.Thick.01.a0.360101670027_00009  VELA_v2.Thick.01.a0.360101670027   
VELA_v2.Thick.01.a0.370054513216_00003  VELA_v2.Thick.01.a0.370054513216   
VELA_v2.Thick.01.a0.370054513216_00005  VELA_v2.Thick.01.a0.370054513216   
VELA_v2.Thick.01.a0.370054513216_00007  VELA_v2.Thick.01.a0.370054513216   
VELA_v2.Thick.01.a0.370054513216_00008

In [28]:
def AM_finding_calc():
    i=0
    for index,row in sgal_shape_df.iterrows():
        #Importing data
        sgal_cat_s = sgal_shape_df.iloc[i]
        sid=sgal_cat_s['sim_id']
        path=sim_cat.loc[sid]['sim_dir'].replace('from_nas2','Users')
        gax=sim_cat.loc[sid]['galaxynumber']
        idx=sim_cat.loc[sid]['index']
        copy_to_tmp(path,gax,idx)
        
        st.ds = yt.load(os.path.join(_TMP_PATH_,'10MpcBox_csf512_'+idx+'.d'))
        #st.ds = yt.load(sim_cat.loc[sgal_cat_s['sim_id']]['sim_path'].replace('from_nas2','Users'))
        
        print i, '    ', 'gal_num:',sgal_cat_s['galaxynumber'],' snapshot:',  sgal_cat_s['aexp'].round(2), '\n'
        
        #Running the function:
        sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_am(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_am(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_am(0.5kpc)')]]=st.AM_hishuvim(sgal_cat_s,0.5) 
        #sgal_shape_df.iloc[index,[sgal_shape_df.columns.get_loc('stars_am(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_am(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_am(0.5kpc)')]]=st.AM_hishuvim(sgal_cat_s,0.5) 
        if np.isnan(sgal_cat_s['r_dm[kpc]'])==False:
            sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_am(r_dm)'),sgal_shape_df.columns.get_loc('dm_am(r_dm)'),sgal_shape_df.columns.get_loc('gas_am(r_dm)')]]=st.AM_hishuvim(sgal_cat_s,sgal_cat_s['r_dm[kpc]']) 
        if np.isnan(sgal_cat_s['r_dm_half[kpc]'])==False:
            sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_am(r_dm_half)'),sgal_shape_df.columns.get_loc('dm_am(r_dm_half)'),sgal_shape_df.columns.get_loc('gas_am(r_dm_half)')]]=st.AM_hishuvim(sgal_cat_s,sgal_cat_s['r_dm_half[kpc]'])  
        
        purge(sim_cat.loc[sid]['index'])
        
        if i%25==0:
            path_1 = r'/vol/sci/astro/home/adambeilialpha/'
            sgal_shape_df.to_pickle(path_1 + r'/sgal_temp_725_dm_all_3am_'+str(i)+'.pkl')
        
        if len(sgal_shape_df)==i:
            sgal_shape_df.to_pickle(path_1 + r'/sgal_temp_725_dm_all_3am_all.pkl')
            break
        i+=1


In [ ]:
AM_finding_calc()

yt : [INFO     ] 2019-12-31 09:44:18,955 discovered particle_data:/tmp/TBOFGFACMNSC/PMcrs0a0.190.DAT
yt : [INFO     ] 2019-12-31 09:44:18,966 discovered particle_header:/tmp/TBOFGFACMNSC/PMcrda0.190.DAT
yt : [INFO     ] 2019-12-31 09:44:18,968 discovered particle_stars:/tmp/TBOFGFACMNSC/stars_a0.190.dat
yt : [INFO     ] 2019-12-31 09:44:19,419 Using root level of 12
yt : [INFO     ] 2019-12-31 09:44:19,433 Discovered 5 species of particles
yt : [INFO     ] 2019-12-31 09:44:19,434 Particle populations:   8567808    451584     63712   2065398     98871 
yt : [INFO     ] 2019-12-31 09:44:19,757 Max level is 10
yt : [INFO     ] 2019-12-31 09:44:19,881 Parameters: current_time              = 4.672131582441644e+16
yt : [INFO     ] 2019-12-31 09:44:19,882 Parameters: domain_dimensions         = [128 128 128]
yt : [INFO     ] 2019-12-31 09:44:19,884 Parameters: domain_left_edge          = [0. 0. 0.]
yt : [INFO     ] 2019-12-31 09:44:19,885 Parameters: domain_right_edge         = [1. 1. 1.]
yt 

0      gal_num: 01  snapshot: 0.19 



yt : [INFO     ] 2019-12-31 09:44:23,988 Loading field plugins.
yt : [INFO     ] 2019-12-31 09:44:23,991 Loaded angular_momentum (8 new fields)
yt : [INFO     ] 2019-12-31 09:44:23,994 Loaded astro (15 new fields)
yt : [INFO     ] 2019-12-31 09:44:23,997 Loaded cosmology (22 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,001 Loaded fluid (66 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,005 Loaded fluid_vector (98 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,008 Loaded geometric (114 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,011 Loaded local (114 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,014 Loaded magnetic_field (122 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,016 Loaded my_plugins (122 new fields)
yt : [INFO     ] 2019-12-31 09:44:24,019 Loaded species (124 new fields)
/cs/sci/sharonl/miniconda/envs/iyt32/lib/python2.7/site-packages/yt/units/yt_array.py:1030: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tu

Importing star data
Importing dark matter data
Importing gas data


In [ ]:
s=time.time()
AM_finding_calc()
e=time.time()
print e-s

yt : [INFO     ] 2019-12-17 22:49:46,667 discovered particle_data:/tmp/RKYPTUNQPLTK/PMcrs0a0.230.DAT
yt : [INFO     ] 2019-12-17 22:49:46,675 discovered particle_header:/tmp/RKYPTUNQPLTK/PMcrda0.230.DAT
yt : [INFO     ] 2019-12-17 22:49:46,681 discovered particle_stars:/tmp/RKYPTUNQPLTK/stars_a0.230.dat
yt : [INFO     ] 2019-12-17 22:49:46,695 Using root level of 14
yt : [INFO     ] 2019-12-17 22:49:46,701 Discovered 7 species of particles
yt : [INFO     ] 2019-12-17 22:49:46,706 Particle populations:  34930688   4943872    855040    139392     21776   2088309   1176113 
yt : [INFO     ] 2019-12-17 22:49:46,973 Max level is 12
yt : [INFO     ] 2019-12-17 22:49:47,014 Parameters: current_time              = 6.210889216424588e+16
yt : [INFO     ] 2019-12-17 22:49:47,018 Parameters: domain_dimensions         = [128 128 128]
yt : [INFO     ] 2019-12-17 22:49:47,022 Parameters: domain_left_edge          = [0. 0. 0.]
yt : [INFO     ] 2019-12-17 22:49:47,025 Parameters: domain_right_edge     

350      gal_num: 07  snapshot: 0.23 



yt : [INFO     ] 2019-12-17 22:49:56,247 Loading field plugins.
yt : [INFO     ] 2019-12-17 22:49:56,251 Loaded angular_momentum (8 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,254 Loaded astro (15 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,257 Loaded cosmology (22 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,260 Loaded fluid (66 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,263 Loaded fluid_vector (98 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,267 Loaded geometric (114 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,269 Loaded local (114 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,272 Loaded magnetic_field (122 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,275 Loaded my_plugins (122 new fields)
yt : [INFO     ] 2019-12-17 22:49:56,278 Loaded species (124 new fields)
/cs/sci/sharonl/miniconda/envs/iyt32/lib/python2.7/site-packages/yt/units/yt_array.py:1030: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tu

Importing star data
Importing dark matter data
Importing gas data
Importing star data
Importing dark matter data
Importing gas data
Importing star data
Importing dark matter data


yt : [INFO     ] 2019-12-17 23:00:12,839 discovered particle_data:/tmp/RKYPTUNQPLTK/PMcrs0a0.230.DAT
yt : [INFO     ] 2019-12-17 23:00:12,845 discovered particle_header:/tmp/RKYPTUNQPLTK/PMcrda0.230.DAT
yt : [INFO     ] 2019-12-17 23:00:12,849 discovered particle_stars:/tmp/RKYPTUNQPLTK/stars_a0.230.dat


...

494      gal_num: 07  snapshot: 0.31 

Importing star data
Importing dark matter data
Importing gas data
Importing star data
Importing dark matter data
Importing gas data


yt : [INFO     ] 2019-12-19 01:21:23,398 discovered particle_data:/tmp/RKYPTUNQPLTK/PMcrs0a0.310.DAT
yt : [INFO     ] 2019-12-19 01:21:23,405 discovered particle_header:/tmp/RKYPTUNQPLTK/PMcrda0.310.DAT
yt : [INFO     ] 2019-12-19 01:21:23,411 discovered particle_stars:/tmp/RKYPTUNQPLTK/stars_a0.310.dat


495      gal_num: 07  snapshot: 0.31 

Importing star data
Importing dark matter data
Importing gas data
Importing star data
Importing dark matter data
Importing gas data


yt : [INFO     ] 2019-12-19 01:29:57,291 discovered particle_data:/tmp/RKYPTUNQPLTK/PMcrs0a0.310.DAT
yt : [INFO     ] 2019-12-19 01:29:57,299 discovered particle_header:/tmp/RKYPTUNQPLTK/PMcrda0.310.DAT
yt : [INFO     ] 2019-12-19 01:29:57,305 discovered particle_stars:/tmp/RKYPTUNQPLTK/stars_a0.310.dat


496      gal_num: 07  snapshot: 0.31 

Importing star data
Importing dark matter data
Importing gas data
Importing star data
Importing dark matter data
Importing gas data


# TESTING GROUND FOR ASSIGNING CELL VALUES
i=2
sgal_cat_s = sgal_shape_df.iloc[i]
st.ds = yt.load(sim_cat.loc[sgal_cat_s['sim_id']]['sim_path'].replace('from_nas2','Users'))
#gal_shape_df.loc[i,['stars_am(1kpc)','dm_am(1kpc)','gas_am(1kpc)']]=st.AM_hishuvim(sgal_cat_s,1)
sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_am(1kpc)'),sgal_shape_df.columns.get_loc('dm_am(1kpc)'),sgal_shape_df.columns.get_loc('gas_am(1kpc)')]]=st.AM_hishuvim(sgal_cat_s,1) 

In [81]:
path_1 = r'/vol/sci/astro/home/adambeilialpha/'
sgal_shape_df = pd.read_pickle(path_1 + r'/sgal_temp_725_dm_all_3am_250.pkl')

In [3]:
sgal_shape_df.iloc[284]['stars_am(0.9coldgas)']

NameError: name 'sgal_shape_df' is not defined

In [163]:
sgal_shape_df.rename(columns={'Rcoldgass_0.9[kpc]':'Rcoldgas_0.9[kpc]'},inplace=True)

In [15]:
def radius_finding_calc_tmp():
    i=0
                               
    for index, row in sgal_shape_df.iterrows():
        #Checking if already run on this row
        if sgal_temp.iloc[i]['calculated']==True:
            i+=1
            continue
        
        sgal_cat_s = sgal_shape_df.iloc[i]
        sid=sgal_cat_s['sim_id']
        path=sim_cat.loc[sid]['sim_dir'].replace('from_nas2','Users')
        gax=sim_cat.loc[sid]['galaxynumber']
        idx=sim_cat.loc[sid]['index']
        copy_to_tmp(path,gax,idx)
        
        st.ds = yt.load(os.path.join(_TMP_PATH_,'10MpcBox_csf512_'+idx+'.d'))    
        #Importing data
        #sgal_cat_s = sgal_temp.iloc[i]
        #st.ds = yt.load(sim_cat.loc[sgal_cat_s['sim_id']]['sim_path'].replace('from_nas2','Users'))
        
        #function that makes the sphere
        #st.get_sp(sgal_cat_s)
        
        #running shapetensor(r) function on the current galaxy
        print i, '    ', 'gal_num:',sgal_cat_s['galaxynumber'],' snapshot:',  sgal_cat_s['aexp'].round(2), '\n'
        
        #sgal_shape_df.loc[index,['r_der','r_1min','r_dm','r_dm_half'] = st.return_rad(sgal_cat_s)
        print "1kpc",'\n'    
        sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_a(1kpc)'),sgal_shape_df.columns.get_loc('stars_b(1kpc)'),sgal_shape_df.columns.get_loc('stars_c(1kpc)'),sgal_shape_df.columns.get_loc('stars_a_vec(1kpc)'),sgal_shape_df.columns.get_loc('stars_b_vec(1kpc)'),sgal_shape_df.columns.get_loc('stars_c_vec(1kpc)'),sgal_shape_df.columns.get_loc('stars(1kpc)_errs'),sgal_shape_df.columns.get_loc('stars(1kpc)_px_start'),sgal_shape_df.columns.get_loc('stars(1kpc)_px_end'),sgal_shape_df.columns.get_loc('stars(1kpc)_iters'),sgal_shape_df.columns.get_loc('stars(1kpc)_err_msg'),
                          sgal_shape_df.columns.get_loc('dm_a(1kpc)'),sgal_shape_df.columns.get_loc('dm_b(1kpc)'),sgal_shape_df.columns.get_loc('dm_c(1kpc)'),sgal_shape_df.columns.get_loc('dm_a_vec(1kpc)'),sgal_shape_df.columns.get_loc('dm_b_vec(1kpc)'),sgal_shape_df.columns.get_loc('dm_c_vec(1kpc)'),sgal_shape_df.columns.get_loc('dm(1kpc)_errs'),sgal_shape_df.columns.get_loc('dm(1kpc)_px_start'),sgal_shape_df.columns.get_loc('dm(1kpc)_px_end'),sgal_shape_df.columns.get_loc('dm(1kpc)_iters'),sgal_shape_df.columns.get_loc('dm(1kpc)_err_msg'),
                          sgal_shape_df.columns.get_loc('gas_a(1kpc)'),sgal_shape_df.columns.get_loc('gas_b(1kpc)'),sgal_shape_df.columns.get_loc('gas_c(1kpc)'),sgal_shape_df.columns.get_loc('gas_a_vec(1kpc)'),sgal_shape_df.columns.get_loc('gas_b_vec(1kpc)'),sgal_shape_df.columns.get_loc('gas_c_vec(1kpc)'),sgal_shape_df.columns.get_loc('gas(1kpc)_errs'),sgal_shape_df.columns.get_loc('gas(1kpc)_px_start'),sgal_shape_df.columns.get_loc('gas(1kpc)_px_end'),sgal_shape_df.columns.get_loc('gas(1kpc)_iters'),sgal_shape_df.columns.get_loc('gas(1kpc)_err_msg')
                          ]] = st.shapetensor(sgal_cat_s,1)
        print '\n'
        print "0.5kpc", '\n'
        sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_a(0.5kpc)'),sgal_shape_df.columns.get_loc('stars_b(0.5kpc)'),sgal_shape_df.columns.get_loc('stars_c(0.5kpc)'),sgal_shape_df.columns.get_loc('stars_a_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('stars_b_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('stars_c_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('stars(0.5kpc)_errs'),sgal_shape_df.columns.get_loc('stars(0.5kpc)_px_start'),sgal_shape_df.columns.get_loc('stars(0.5kpc)_px_end'),sgal_shape_df.columns.get_loc('stars(0.5kpc)_iters'),sgal_shape_df.columns.get_loc('stars(0.5kpc)_err_msg'),
                          sgal_shape_df.columns.get_loc('dm_a(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_b(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_c(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_a_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_b_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('dm_c_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('dm(0.5kpc)_errs'),sgal_shape_df.columns.get_loc('dm(0.5kpc)_px_start'),sgal_shape_df.columns.get_loc('dm(0.5kpc)_px_end'),sgal_shape_df.columns.get_loc('dm(0.5kpc)_iters'),sgal_shape_df.columns.get_loc('dm(0.5kpc)_err_msg'),
                          sgal_shape_df.columns.get_loc('gas_a(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_b(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_c(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_a_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_b_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('gas_c_vec(0.5kpc)'),sgal_shape_df.columns.get_loc('gas(0.5kpc)_errs'),sgal_shape_df.columns.get_loc('gas(0.5kpc)_px_start'),sgal_shape_df.columns.get_loc('gas(0.5kpc)_px_end'),sgal_shape_df.columns.get_loc('gas(0.5kpc)_iters'),sgal_shape_df.columns.get_loc('gas(0.5kpc)_err_msg')
                          ]] = st.shapetensor(sgal_cat_s,0.5)
        print '\n'
        print "Rsat", '\n'
        sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_a(Rsat)'),sgal_shape_df.columns.get_loc('stars_b(Rsat)'),sgal_shape_df.columns.get_loc('stars_c(Rsat)'),sgal_shape_df.columns.get_loc('stars_a_vec(Rsat)'),sgal_shape_df.columns.get_loc('stars_b_vec(Rsat)'),sgal_shape_df.columns.get_loc('stars_c_vec(Rsat)'),sgal_shape_df.columns.get_loc('stars(Rsat)_errs'),sgal_shape_df.columns.get_loc('stars(Rsat)_px_start'),sgal_shape_df.columns.get_loc('stars(Rsat)_px_end'),sgal_shape_df.columns.get_loc('stars(Rsat)_iters'),sgal_shape_df.columns.get_loc('stars(Rsat)_err_msg'),
                          sgal_shape_df.columns.get_loc('dm_a(Rsat)'),sgal_shape_df.columns.get_loc('dm_b(Rsat)'),sgal_shape_df.columns.get_loc('dm_c(Rsat)'),sgal_shape_df.columns.get_loc('dm_a_vec(Rsat)'),sgal_shape_df.columns.get_loc('dm_b_vec(Rsat)'),sgal_shape_df.columns.get_loc('dm_c_vec(Rsat)'),sgal_shape_df.columns.get_loc('dm(Rsat)_errs'),sgal_shape_df.columns.get_loc('dm(Rsat)_px_start'),sgal_shape_df.columns.get_loc('dm(Rsat)_px_end'),sgal_shape_df.columns.get_loc('dm(Rsat)_iters'),sgal_shape_df.columns.get_loc('dm(Rsat)_err_msg'),
                          sgal_shape_df.columns.get_loc('gas_a(Rsat)'),sgal_shape_df.columns.get_loc('gas_b(Rsat)'),sgal_shape_df.columns.get_loc('gas_c(Rsat)'),sgal_shape_df.columns.get_loc('gas_a_vec(Rsat)'),sgal_shape_df.columns.get_loc('gas_b_vec(Rsat)'),sgal_shape_df.columns.get_loc('gas_c_vec(Rsat)'),sgal_shape_df.columns.get_loc('gas(Rsat)_errs'),sgal_shape_df.columns.get_loc('gas(Rsat)_px_start'),sgal_shape_df.columns.get_loc('gas(Rsat)_px_end'),sgal_shape_df.columns.get_loc('gas(Rsat)_iters'),sgal_shape_df.columns.get_loc('gas(Rsat)_err_msg')
                          ]] = st.shapetensor(sgal_cat_s,sgal_cat_s['Rsat[kpc]'])
        print '\n'
        print "0.9coldgas", '\n'                  
        sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('stars_a(1kpc)'),sgal_shape_df.columns.get_loc('stars_b(1kpc)'),sgal_shape_df.columns.get_loc('stars_c(1kpc)'),sgal_shape_df.columns.get_loc('stars_a_vec(1kpc)'),sgal_shape_df.columns.get_loc('stars_b_vec(1kpc)'),sgal_shape_df.columns.get_loc('stars_c_vec(1kpc)'),sgal_shape_df.columns.get_loc('stars(1kpc)_errs'),sgal_shape_df.columns.get_loc('stars(1kpc)_px_start'),sgal_shape_df.columns.get_loc('stars(1kpc)_px_end'),sgal_shape_df.columns.get_loc('stars(1kpc)_iters'),sgal_shape_df.columns.get_loc('stars(1kpc)_err_msg'),
                          sgal_shape_df.columns.get_loc('dm_a(1kpc)'),sgal_shape_df.columns.get_loc('dm_b(1kpc)'),sgal_shape_df.columns.get_loc('dm_c(1kpc)'),sgal_shape_df.columns.get_loc('dm_a_vec(1kpc)'),sgal_shape_df.columns.get_loc('dm_b_vec(1kpc)'),sgal_shape_df.columns.get_loc('dm_c_vec(1kpc)'),sgal_shape_df.columns.get_loc('dm(1kpc)_errs'),sgal_shape_df.columns.get_loc('dm(1kpc)_px_start'),sgal_shape_df.columns.get_loc('dm(1kpc)_px_end'),sgal_shape_df.columns.get_loc('dm(1kpc)_iters'),sgal_shape_df.columns.get_loc('dm(1kpc)_err_msg'),
                          sgal_shape_df.columns.get_loc('gas_a(1kpc)'),sgal_shape_df.columns.get_loc('gas_b(1kpc)'),sgal_shape_df.columns.get_loc('gas_c(1kpc)'),sgal_shape_df.columns.get_loc('gas_a_vec(1kpc)'),sgal_shape_df.columns.get_loc('gas_b_vec(1kpc)'),sgal_shape_df.columns.get_loc('gas_c_vec(1kpc)'),sgal_shape_df.columns.get_loc('gas(1kpc)_errs'),sgal_shape_df.columns.get_loc('gas(1kpc)_px_start'),sgal_shape_df.columns.get_loc('gas(1kpc)_px_end'),sgal_shape_df.columns.get_loc('gas(1kpc)_iters'),sgal_shape_df.columns.get_loc('gas(1kpc)_err_msg')
                          ]] = st.shapetensor(sgal_cat_s,1)
       sgal_shape_df.iloc[i,[sgal_shape_df.columns.get_loc('calculated')]]=True
        
        #saving the loop every 25 iterations in a new pkl
        #saving the time it took to run those 25 iters as time(s)
        if i%25==0:
            e=time.time()
            path_1 = r'/vol/sci/astro/home/adambeilialpha/'
            sgal_shape_df.to_pickle(path_1 + r'/sgal_temp_sukkot_'+str(i)+'.pkl')
        #if 300==i:
        #    break
        i+=1    
    

In [18]:
sgal_shape_df.loc[2802,['stars_a(1kpc)']]=1

In [19]:
sgal_shape_df.iloc[2802]['stars_a(1kpc)']

nan

In [45]:
def dm_radius_calc():
    i=1400
    
    for index, row in sgal_shape_df_tmp.iterrows():
        #Importing data
        sgal_cat_s = sgal_shape_df_tmp.iloc[i]
        st.ds = yt.load(sim_cat.loc[sgal_cat_s['sim_id']]['sim_path'].replace('from_nas2','Users'))
        #function that makes the sphere
        st.get_sp(sgal_cat_s)
        
        #running shapetensor(r) function on the current galaxy
        print i, 'gal_num:',sgal_cat_s['galaxynumber'],' snapshot:',  sgal_cat_s['aexp'].round(2)
        
        sgal_shape_df_tmp.iloc[i,[sgal_shape_df_tmp.columns.get_loc('r_der[kpc]'),sgal_shape_df_tmp.columns.get_loc('r_1min[kpc]'),
                                      sgal_shape_df_tmp.columns.get_loc('r_dm[kpc]'),sgal_shape_df_tmp.columns.get_loc('r_dm_half[kpc]')]]=st.return_rad(sgal_cat_s)
        #[index,['r_der[kpc]','r_1min[kpc]','r_dm[kpc]','r_dm_half[kpc]']] = st.return_rad(sgal_cat_s)
        
        #if i==1431:
        #    path_1 = r'/vol/sci/astro/home/adambeilialpha/'
        #    sgal_shape_df_tmp.to_pickle(path_1 + r'/NEW_sgal_temp_sukkot_725_r_dm'+str(i)+'.pkl')
        if i%500==0:
            path_1 = r'/vol/sci/astro/home/adambeilialpha/'
            sgal_shape_df_tmp.to_pickle(path_1 + r'/NEW_sgal_temp_sukkot_725_r_dm'+str(i)+'.pkl')
        if i==2803:
            path_1 = r'/vol/sci/astro/home/adambeilialpha/'
            sgal_shape_df_tmp.to_pickle(path_1 + r'/sgal_temp_sukkot_725_r_dm_all_final.pkl')
        i+=1

In [46]:
s=time.time()
dm_radius_calc()
e=time.time()
print e-s

yt : [INFO     ] 2019-12-09 22:40:09,694 discovered particle_data:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/PMcrs0a0.450.DAT
yt : [INFO     ] 2019-12-09 22:40:09,759 discovered particle_header:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/PMcrda0.450.DAT
yt : [INFO     ] 2019-12-09 22:40:09,825 discovered particle_stars:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/stars_a0.450.dat


1400 gal_num: 10  snapshot: 0.45
a: 5377
b: [0.03190942 0.04022665 0.05840371 ... 3.29691638 3.29743789 3.29787677] kpc


yt : [INFO     ] 2019-12-09 22:40:31,323 discovered particle_data:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/PMcrs0a0.450.DAT
yt : [INFO     ] 2019-12-09 22:40:31,388 discovered particle_header:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/PMcrda0.450.DAT


a: 2688
b: [0.03190942 0.04022665 0.05840371 ... 3.09222211 3.09223482 3.09313718] kpc
r_der =  20763.4673594
r_1min =  3.3000005250333304
r_dm =  3.0931371832948176
r_dm_half =  1.9434641103935555


yt : [INFO     ] 2019-12-09 22:40:31,457 discovered particle_stars:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/stars_a0.450.dat


...

yt : [INFO     ] 2019-12-11 19:18:16,433 discovered particle_data:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_34/PMcrs0a0.340.DAT
yt : [INFO     ] 2019-12-11 19:18:16,464 discovered particle_header:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_34/PMcrda0.340.DAT
yt : [INFO     ] 2019-12-11 19:18:16,496 discovered particle_stars:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_34/stars_a0.340.dat
yt : [INFO     ] 2019-12-11 19:18:16,678 Using root level of 13
yt : [INFO     ] 2019-12-11 19:18:16,726 Discovered 6 species of particles
yt : [INFO     ] 2019-12-11 19:18:16,728 Particle populations:  30220288   2303488    345024     51192   2073485   6472146 
yt : [INFO     ] 2019-12-11 19:18:16,912 Max level is 12
yt : [INFO     ] 2019-12-11 19:18:16,933 Parameters: current_time              = 1.1031749008689296e+17
yt : [INFO     ] 2019-12-11 19:18:16,936 Parameters: domain_dimensions         = [128 128 128]
yt : [INFO     ] 2019-12-11 19:18:16,939 Parameter

2801 gal_num: 34  snapshot: 0.34
a: 81410
b: [0.04147025 0.0850197  0.09077587 ... 8.02491115 8.02495139 8.02497593] kpc
a: 40704
b: [0.04147025 0.0850197  0.09077587 ... 7.66382894 7.66387561 7.66399155] kpc
r_der =  7702.31545953
r_1min =  8.02500020407641
r_dm =  7.663996900988198
r_dm_half =  5.7044297560448385


yt : [INFO     ] 2019-12-11 19:19:09,486 discovered particle_data:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_34/PMcrs0a0.350.DAT
yt : [INFO     ] 2019-12-11 19:19:09,515 discovered particle_header:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_34/PMcrda0.350.DAT
yt : [INFO     ] 2019-12-11 19:19:09,544 discovered particle_stars:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_34/stars_a0.350.dat
yt : [INFO     ] 2019-12-11 19:19:09,761 Using root level of 13
yt : [INFO     ] 2019-12-11 19:19:09,800 Discovered 6 species of particles
yt : [INFO     ] 2019-12-11 19:19:09,803 Particle populations:  30220288   2303488    345024     51192   2073485   8307001 
yt : [INFO     ] 2019-12-11 19:19:09,967 Max level is 12
yt : [INFO     ] 2019-12-11 19:19:09,985 Parameters: current_time              = 1.1496940477176686e+17
yt : [INFO     ] 2019-12-11 19:19:09,987 Parameters: domain_dimensions         = [128 128 128]
yt : [INFO     ] 2019-12-11 19:19:09,990 Parameter

2802 gal_num: 34  snapshot: 0.35
a: 6200
b: [0.01644152 0.06490492 0.06843804 ... 4.04864922 4.04886954 4.04988756] kpc
a: 3099
b: [0.01644152 0.06490492 0.06843804 ... 3.85234297 3.85245557 3.85252293] kpc
r_der =  7918.67263536
r_1min =  4.050000860829841
r_dm =  3.8525764801737585
r_dm_half =  2.760332736502794


IndexError: single positional indexer is out-of-bounds

In [116]:
e=time.time()

In [117]:
print e-s

162613.821946


In [110]:
sgal_shape_df.to_pickle(path_1 + r'/sgal_temp_sukkot_725_dm_all.pkl')

In [332]:
path_1 = r'/vol/sci/astro/home/adambeilialpha/'

In [113]:
sgal_shape_df = pd.read_pickle(path_1 + r'/sgal_temp_sukkot_725_dm_all.pkl')

In [65]:
sgal_cat_s = sgal_shape_df.iloc[1428]
ds = yt.load(sim_cat.loc[sgal_cat_s['sim_id']]['sim_path'].replace('from_nas2','Users'))

yt : [INFO     ] 2019-11-08 12:35:25,060 discovered particle_data:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/PMcrs0a0.510.DAT
yt : [INFO     ] 2019-11-08 12:35:25,126 discovered particle_header:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/PMcrda0.510.DAT
yt : [INFO     ] 2019-11-08 12:35:25,192 discovered particle_stars:/vol/sci/astro/cosmo/nas2/Users/ceverino/VELA_v2/VELA_v2_10/stars_a0.510.dat


In [89]:
x=YTQuantity(sgal_shape_df.iloc[1428]['x[kpc]'])*kpc

a = ds.quan((sgal_shape_df.iloc[1429]['x[kpc]']-sgal_shape_df.iloc[1429]['Rsat[kpc]']), 'kpc')
a.in_units('code_length')

0.49685577401175324 code_length

In [66]:
print ("Length unit: ", ds.length_unit.in_units('code_length'))

('Length unit: ', 1.0 code_length)


In [86]:
path_1 = r'/vol/sci/astro/home/adambeilialpha/'
times = pd.read_pickle(path_1 + r'/sgal_temp_run_times(s)')

In [87]:
times

time(s)
0     236.628345
1     197.876088
2     197.736403
3     189.445396
4     158.154975
5     158.173666
6     153.229416
7    1322.960687
8            NaN
9            NaN
10           NaN
11           NaN
12           NaN
13           NaN
14           NaN
15           NaN
16           NaN
17           NaN
18           NaN
19           NaN
20           NaN
21           NaN
22           NaN
23           NaN
24           NaN
25           NaN
26           NaN
27           NaN
28           NaN
29           NaN
30           NaN
31           NaN
32           NaN
33           NaN
34           NaN
35           NaN
36           NaN
37           NaN
38           NaN
39           NaN
40           NaN
41           NaN
42           NaN
43           NaN
44           NaN
45           NaN
46           NaN
47           NaN
48           NaN
49           NaN
50           NaN
51           NaN
52           NaN
53           NaN
54           NaN
55           NaN
56           NaN
57           NaN
58           NaN
59           NaN
60           NaN
61           NaN
62           NaN
63           NaN
64           NaN
65           NaN
66           NaN
67           NaN
68           NaN
69           NaN
70           NaN
71           NaN
72           NaN
73           NaN
74           NaN
75           NaN
76           NaN
77           NaN
78           NaN
79           NaN
80           NaN
81           NaN
82           NaN
83           NaN
84           NaN
85           NaN
86           NaN
87           NaN
88           NaN
89           NaN
90           NaN
91           NaN
92           NaN
93           NaN
94           NaN
95           NaN
96           NaN
97           NaN
98           NaN
99           NaN
100          NaN
101          NaN
102          NaN
103          NaN
104          NaN
105          NaN
106          NaN
107          NaN
108          NaN
109          NaN
110          NaN
111          NaN

In [100]:
len(sgal_shape_df)

2803

In [ ]:
###CHECK HOW MANY ERROR MESSAGES ARE IN THE SHAPES (COMPARED TO HOW MANY NON ERROR MSGS)
a=sgal_shape_df_tmp.iloc[:730]['stars(1kpc)_err_msg']
b=sgal_shape_df_tmp.iloc[:730]['dm(1kpc)_err_msg']
c=sgal_shape_df_tmp.iloc[:730]['gas(1kpc)_err_msg']
d=sgal_shape_df_tmp.iloc[:730]['stars(0.5kpc)_err_msg']
e=sgal_shape_df_tmp.iloc[:730]['dm(0.5kpc)_err_msg']
f=sgal_shape_df_tmp.iloc[:730]['gas(0.5kpc)_err_msg']
g=sgal_shape_df_tmp.iloc[:730]['stars(Rsat)_err_msg']
h=sgal_shape_df_tmp.iloc[:730]['dm(Rsat)_err_msg']
i=sgal_shape_df_tmp.iloc[:730]['gas(Rsat)_err_msg']
j=sgal_shape_df_tmp.iloc[:730]['stars(0.9coldgas)_err_msg']
k=sgal_shape_df_tmp.iloc[:730]['dm(0.9coldgas)_err_msg']
l=sgal_shape_df_tmp.iloc[:730]['gas(0.9coldgas)_err_msg']

In [108]:
#SETTING UP NEW COLUMNS IN sgal_shape_df

sgal_shape_df['stars_am(1kpc)'],sgal_shape_df['dm_am(1kpc)'],sgal_shape_df['gas_am(1kpc)'] = [[np.zeros((1,3))]*2803]*3
sgal_shape_df['stars_am(0.5kpc)'],sgal_shape_df['dm_am(0.5kpc)'],sgal_shape_df['gas_am(0.5kpc)'] = [[np.zeros((1,3))]*2803]*3
sgal_shape_df['stars_am(Rsat)'],sgal_shape_df['dm_am(Rsat)'],sgal_shape_df['gas_am(Rsat)'] = [[np.zeros((1,3))]*2803]*3
sgal_shape_df['stars_am(0.9coldgas)'],sgal_shape_df['dm_am(0.9coldgas)'],sgal_shape_df['gas_am(0.9coldgas)'] = [[np.zeros((1,3))]*2803]*3
sgal_shape_df['stars_am(r_dm)'],sgal_shape_df['dm_am(r_dm)'],sgal_shape_df['gas_am(r_dm)'] = [[np.zeros((1,3))]*2803]*3
sgal_shape_df['stars_am(r_dm_half)'],sgal_shape_df['dm_am(r_dm_half)'],sgal_shape_df['gas_am(r_dm_half)'] = [[np.zeros((1,3))]*2803]*3



In [21]:
sgal_shape_df['r_der[kpc]'],sgal_shape_df['r_1min[kpc]'],sgal_shape_df['r_dm[kpc]'],sgal_shape_df['r_dm_half[kpc]'] = [np.nan]*4